# 🏠  Egypt Real Estate Listings

## Abstract  
##### This project focuses on analyzing and predicting real estate prices in Egypt using a dataset containing thousands of property listings. The dataset includes features such as location, area, number of rooms, bathrooms, and property type, along with price information. The goal of this project is to build a complete data analysis pipeline that automates data cleaning, preprocessing, visualization, and modeling using Python libraries like NumPy, Pandas, Matplotlib, and Seaborn. Insights from this dataset can help identify market trends, understand factors affecting housing prices, and support better real estate investment decisions.  

## Dataset Summary  
##### The dataset contains 19924 rows and 11 features & multiple property listings across different Egyptian cities and regions, with details about each property’s characteristics and pricing. It includes numerical features such as area and price, as well as categorical attributes like city, property type, and furnishing status. The dataset contains around several thousand rows and multiple columns describing each listing. Key problems detected include missing values, non-numeric symbols within numeric fields (e.g., “1,200 EGP”, “250 sqm”), inconsistent text formats, duplicated rows, and outliers in property prices and sizes. These issues will be resolved through preprocessing before performing exploratory analysis and machine learning modeling to predict property prices.


#  Data Cleaning Process
## This section focuses on cleaning, fixing, and preparing the dataset for analysis and modeling.


## Step 1: Standardize Column Names

In [47]:
import pandas as pd

In [46]:
df = pd.read_csv("egypt_real_estate_listings.csv", encoding='utf-8')


In [8]:
# Convert all column names to lowercase and replace spaces or special characters
df.columns = (
    df.columns
    .str.strip()          # Remove leading/trailing spaces
    .str.lower()          # Convert to lowercase
    .str.replace(' ', '_')# Replace spaces with underscores
    .str.replace('-', '_')# Replace hyphens with underscores
)


In [9]:
# Display the cleaned column names
df.columns.tolist()

['url',
 'price',
 'description',
 'location',
 'type',
 'size',
 'bedrooms',
 'bathrooms',
 'available_from',
 'payment_method',
 'down_payment']

## Step 2: Clean numeric columns before filling missing values

In [10]:
# ✅ Step: Extract and clean property size properly

# Ensure column is string
df['size'] = df['size'].astype(str)

# Extract sqm if available
df['size_sqm'] = df['size'].str.extract(r'/\s*(\d+\.?\d*)\s*sqm')[0]

# Extract sqft if sqm is missing
mask_missing = df['size_sqm'].isna()
df.loc[mask_missing, 'size_sqm'] = (
    df.loc[mask_missing, 'size']
    .str.extract(r'(\d+\.?\d*)\s*sqft')[0]
    .astype(float) * 0.093  # Convert sqft → sqm
)

# Convert to float
df['size_sqm'] = df['size_sqm'].astype(float)

# Drop the old 'size' column
df.drop(columns=['size'], inplace=True)

# ✅ Verify result
df[['price', 'down_payment', 'size_sqm']].head()


price   down_payment  size_sqm
0   8,000,000  1,200,000 EGP      68.0
1  25,000,000  2,100,000 EGP     220.0
2  15,135,000  1,513,000 EGP     118.0
3  12,652,000  1,260,000 EGP     166.0
4  45,250,000  2,262,500 EGP     400.0

## Step 3: Add derived columns

In [11]:
#  تنظيف السعر والدفعة قبل التحويل للأرقام
df['price'] = (
    df['price']
    .astype(str)
    .str.replace(',', '', regex=False)      # يشيل الفواصل
    .str.replace('EGP', '', regex=False)    # يشيل كلمة EGP
    .str.replace(r'[^\d.]', '', regex=True) # يشيل أي رموز تانية
)

df['down_payment'] = (
    df['down_payment']
    .astype(str)
    .str.replace(',', '', regex=False)
    .str.replace('EGP', '', regex=False)
    .str.replace(r'[^\d.]', '', regex=True)
)


In [12]:
# نتأكد إن price و down_payment أرقام
df['price'] = pd.to_numeric(df['price'], errors='coerce')
df['down_payment'] = pd.to_numeric(df['down_payment'], errors='coerce')
# نحسب نسبة الدفعة المقدمة إلى السعر
df["down_payment_ratio"] = (df["down_payment"] / df["price"]).round(2)
# تعويض القيم غير المنطقية (مثلاً أكبر من 1 أو أقل من 0.01)
invalid_ratio = (df['down_payment_ratio'] < 0.01) | (df['down_payment_ratio'] > 0.8)



In [13]:
df.head()

url       price                                        description  \
0  https://www.propertyfinder.eg/en/plp/buy/chale...   8000000.0  OWN A CHALET IN EL GOUNA WITH A PRIME LOCATION...   
1  https://www.propertyfinder.eg/en/plp/buy/villa...  25000000.0  For sale, a villa with immediate delivery in C...   
2  https://www.propertyfinder.eg/en/plp/buy/chale...  15135000.0  With a down payment of EGP 1,513,000, a fully ...   
3  https://www.propertyfinder.eg/en/plp/buy/apart...  12652000.0  Own an apartment in New Cairo with a minimal d...   
4  https://www.propertyfinder.eg/en/plp/buy/villa...  45250000.0  Project: Granville\nLocation: Fifth Settlement...   

                                            location       type bedrooms bathrooms available_from payment_method  \
0       Swan Lake Gouna, Al Gouna, Hurghada, Red Sea     Chalet  1+ Maid         1    31 Aug 2025           Cash   
1   Karmell, New Zayed City, Sheikh Zayed City, Giza      Villa        4         4     2 Sep 2025           Cash   
2              Azha North, Ras Al Hekma, North Coast     Chalet        2         2    19 Aug 2025           Cash   
3  Taj City, 5th Settlement Compounds, The 5th Se...  Apartment        3         2    26 Aug 2025   Installments   
4                 Granville, New Capital City, Cairo      Villa        7         7     2 Sep 2025           Cash   

   down_payment  size_sqm  down_payment_ratio  
0     1200000.0      68.0                0.15  
1     2100000.0     220.0                0.08  
2     1513000.0     118.0                0.10  
3     1260000.0     166.0                0.10  
4     2262500.0     400.0                0.05

In [14]:
# تحويل العمود لتاريخ حقيقي
df['available_from'] = pd.to_datetime(df['available_from'], errors='coerce')

# استخراج السنة والشهر
df['year'] = df['available_from'].dt.year

# تحويل رقم الشهر لاسم الشهر (January, February, ...)
df['month'] = df['available_from'].dt.strftime('%B')


df['year'] = df['year'].astype('Int64')  
df['month'] = df['month'].astype(str)

# step 4: Fix unrealistic values


##  Handle unrealistic prices

In [15]:
df.loc[(df['price'] < 500_000) | (df['price'] > 100_000_000), 'price'] = np.nan
df['price'] = df['price'].fillna(df['price'].median())

##  Validate down_payment relative to price

In [16]:
df.loc[
    (df['down_payment'] <= 0) |
    (df['down_payment'] > df['price']) |
    (df['down_payment'] < 0.02 * df['price']) |
    (df['down_payment'] > 0.7 * df['price']),
    'down_payment'
] = np.nan

## Fix unrealistic down_payment_ratio

In [17]:
# احسبي النسبة تاني للصفوف اللي فيها price و down_payment لكن النسبة NaN
df.loc[df['down_payment_ratio'].isna(), 'down_payment_ratio'] = (
    df['down_payment'] / df['price']
)
median_ratio = df['down_payment_ratio'].median()
df['down_payment_ratio'] = df['down_payment_ratio'].fillna(median_ratio)


df.loc[
    (df['down_payment'].isna()) | (df['down_payment'] <= 10000),
    'down_payment'
] = df['price'] * df['down_payment_ratio']


print(df['down_payment_ratio'].isna().sum())
print(df['down_payment'].isna().sum())


0
0


In [18]:
print(df['down_payment_ratio'].describe())
print(df['size_sqm'].describe())


count    19924.000000
mean         0.111483
std          0.074290
min          0.000000
25%          0.100000
50%          0.100000
75%          0.100000
max          0.500000
Name: down_payment_ratio, dtype: float64
count    19847.000000
mean       202.597664
std        126.661137
min          0.186000
25%        125.000000
50%        170.000000
75%        239.000000
max        985.000000
Name: size_sqm, dtype: float64


## Validate bedroom & bathroom counts


In [19]:
# Ensure numeric columns are actually numeric
df['bedrooms'] = pd.to_numeric(df['bedrooms'], errors='coerce')
df['bathrooms'] = pd.to_numeric(df['bathrooms'], errors='coerce')

# Now safe to validate
df.loc[(df['bedrooms'] < 1) | (df['bedrooms'] > 7), 'bedrooms'] = np.nan
df.loc[(df['bathrooms'] < 1) | (df['bathrooms'] > 7), 'bathrooms'] = np.nan




## Step 5: Handle Missing Values

In [20]:

# Check percentage of missing values 
missing_percent = df.isnull().mean() * 100
print("Percentage of Missing Values:\n", missing_percent)

# Fill missing numeric values
df['price'] = df['price'].fillna(df['price'].median())
df['size_sqm'] = df['size_sqm'].fillna(df['size_sqm'].median())
df['down_payment'] = df['down_payment'].fillna(df['down_payment'].median())

# Fill missing categorical values
df['bedrooms'] = df['bedrooms'].fillna(df['bedrooms'].mode()[0])
df['bathrooms'] = df['bathrooms'].fillna(df['bathrooms'].mode()[0])
df['available_from'] = df['available_from'].fillna('Unknown')
df['payment_method'] = df['payment_method'].fillna(df['payment_method'].mode()[0])
df['location'] = df['location'].fillna('Unknown')
df['type'] = df['type'].fillna('Unknown')
df['description'] = df['description'].fillna('No description')

# Fill missing in new time columns (year and month_name)
df['year'] = df['year'].fillna(df['year'].mode()[0])
df['month'] = df['month'].fillna('Unknown')

# Ensure year is integer (no .0 in Excel)
df['year'] = df['year'].astype('Int64')
df['month'] = df['month'].astype(str)


Percentage of Missing Values:
 url                    0.000000
price                  0.000000
description            0.391488
location               0.456736
type                   0.386469
bedrooms              49.126681
bathrooms              1.525798
available_from         3.327645
payment_method         2.715318
down_payment           0.000000
size_sqm               0.386469
down_payment_ratio     0.000000
year                   3.327645
month                  0.000000
dtype: float64


In [21]:
# Step X: Clean and fill missing values in 'month' column

# أولاً: نتأكد إن مفيش قيم نصية مكتوبة كأنها NaN
df['month'] = df['month'].replace(['nan', 'NaN', 'None', 'Unknown', '', ' '], np.nan)

# نحسب المود (أكثر شهر متكرر)
month_mode = df['month'].mode()[0]

# نستبدل القيم الناقصة بالمود
df['month'] = df['month'].fillna(month_mode)

print("Missing values in 'month' after filling:", df['month'].isnull().sum())
print("Most frequent month (used to fill NaNs):", month_mode)


Missing values in 'month' after filling: 0
Most frequent month (used to fill NaNs): August


In [22]:
# Verify changes
df.isnull().sum()

url                   0
price                 0
description           0
location              0
type                  0
bedrooms              0
bathrooms             0
available_from        0
payment_method        0
down_payment          0
size_sqm              0
down_payment_ratio    0
year                  0
month                 0
dtype: int64

## Remove unnecessary columns

In [23]:
df = df.drop(columns=['url'], errors='ignore')
df = df.drop(columns=['description'], errors='ignore')
df = df.drop(columns=['available_from'], errors='ignore')

## Step 6: Clean and normalize text columns

In [24]:
text_columns = ['location', 'type', 'payment_method']

for col in text_columns:
    df[col] = (
        df[col]
        .astype(str)                           # Ensure the column is of string type
        .str.strip()                            # Remove leading/trailing spaces
        .str.replace(r'\n', ' ', regex=True)    # Replace line breaks with spaces
        .str.replace(r'\r', '', regex=True)     # Remove carriage returns
        .str.replace(r'\s+', ' ', regex=True)   # Replace multiple spaces with a single space
        .str.lower()                            # Convert all text to lowercase
    )

# Preview cleaned text columns
df[text_columns].head()


location       type payment_method
0       swan lake gouna, al gouna, hurghada, red sea     chalet           cash
1   karmell, new zayed city, sheikh zayed city, giza      villa           cash
2              azha north, ras al hekma, north coast     chalet           cash
3  taj city, 5th settlement compounds, the 5th se...  apartment   installments
4                 granville, new capital city, cairo      villa           cash

## Step 7: Standardize categorical column values

In [25]:
## Step 5: Normalize Categorical Columns (Standardize Property Types & Payment Methods)

# --- Normalize property types ---
# Group similar property types together to reduce category fragmentation
df['type'] = df['type'].replace({
    'apartment': 'apartment',
    'duplex': 'apartment',
    'penthouse': 'apartment',
    'ivilla': 'apartment',
    
    'villa': 'villa',
    'twin house': 'villa',
    'townhouse': 'villa',
    
    'chalet': 'chalet',
    'bungalow': 'chalet',
    'cabin': 'chalet',
    
    'land': 'land',

    # Any other rare or unclear types grouped as "other"
    'palace': 'other',
    'bulk sale unit': 'other',
    'whole building': 'other',
    'full floor': 'other',
    'roof': 'other',
    'hotel apartment': 'other',
    'unknown': 'other'
})

# --- Normalize payment method values ---
df['payment_method'] = df['payment_method'].replace({
    'cash': 'cash',
    'installments': 'installments'
})

# --- Verify normalization ---
print("Unique property types after normalization:\n", df['type'].unique())
print("\nUnique payment methods after normalization:\n", df['payment_method'].unique())


Unique property types after normalization:
 ['chalet' 'villa' 'apartment' 'other' 'land']

Unique payment methods after normalization:
 ['cash' 'installments']


## Step 8: Handle Outliers

In [26]:
## Step 6: Handle Outliers in Numeric Columns (Capping Method)

# Define numeric columns
numeric_columns = ['price', 'size_sqm', 'down_payment']

# Apply capping between the 1st and 99th percentiles
for col in numeric_columns:
    lower = df[col].quantile(0.01)
    upper = df[col].quantile(0.99)
    df[col] = df[col].clip(lower, upper)
    print(f"{col}: capped between {lower:.2f} and {upper:.2f}")

# Verify after capping
df[numeric_columns].describe()


price: capped between 1450000.00 and 74240625.00
size_sqm: capped between 45.00 and 723.54
down_payment: capped between 0.00 and 9000000.00


price      size_sqm  down_payment
count  1.992400e+04  19924.000000  1.992400e+04
mean   1.447986e+07    201.484263  1.514457e+06
std    1.329897e+07    120.904962  1.617173e+06
min    1.450000e+06     45.000000  0.000000e+00
25%    6.000000e+06    125.000000  5.640000e+05
50%    1.020000e+07    170.000000  1.000000e+06
75%    1.750000e+07    238.000000  1.795000e+06
max    7.424063e+07    723.540000  9.000000e+06

# Step 9: Clean and split location column

In [27]:
if 'location' in df.columns:

    # نفصل location إلى أجزاء (مثلاً: "karmell, new zayed city, sheikh zayed city, giza")
    location_split = df['location'].str.split(',', expand=True)

    # ناخد أول 3 أجزاء بس (علشان الباقي ساعات بيكون descriptive زيادة)
    df['area'] = location_split[0].str.strip().str.title()
    df['city'] = location_split[1].str.strip().str.title()
    df['governorate'] = location_split[2].str.strip().str.title()

    # معالجة القيم الفارغة
    df['city'] = df['city'].fillna('Unknown')
    df['governorate'] = df['governorate'].fillna('Unknown')

    # نحذف عمود location الأصلي بعد ما استخرجنا منه البيانات
    df = df.drop(columns=['location'], errors='ignore')

else:
    print("⚠️ No 'location' column found — skipping location cleaning.")


## Step 10: Save the cleaned dataset

In [28]:
df.to_csv("cleaned_dataset.csv", index=False, sep=",", quotechar='"', encoding="utf-8")

print("✅ Clean dataset saved successfully as 'cleaned_real_estate.csv'")
print("Final shape:", df.shape)


✅ Clean dataset saved successfully as 'cleaned_real_estate.csv'
Final shape: (19924, 13)


# Revision

In [29]:
from ydata_profiling import ProfileReport

profile = ProfileReport(df, title="data Report", explorative=True)

profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 13/13 [00:00<00:00, 24.33it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [30]:
df.isnull().sum()

price                 0
type                  0
bedrooms              0
bathrooms             0
payment_method        0
down_payment          0
size_sqm              0
down_payment_ratio    0
year                  0
month                 0
area                  0
city                  0
governorate           0
dtype: int64

In [31]:
df.head()

price       type  bedrooms  bathrooms payment_method  down_payment  size_sqm  down_payment_ratio  year  \
0   8000000.0     chalet       3.0        1.0           cash     1200000.0      68.0                0.15  2025   
1  25000000.0      villa       4.0        4.0           cash     2100000.0     220.0                0.08  2025   
2  15135000.0     chalet       2.0        2.0           cash     1513000.0     118.0                0.10  2025   
3  12652000.0  apartment       3.0        2.0   installments     1260000.0     166.0                0.10  2025   
4  45250000.0      villa       7.0        7.0           cash     2262500.0     400.0                0.05  2025   

       month             area                      city         governorate  
0     August  Swan Lake Gouna                  Al Gouna            Hurghada  
1  September          Karmell            New Zayed City   Sheikh Zayed City  
2     August       Azha North              Ras Al Hekma         North Coast  
3     August         Taj City  5Th Settlement Compounds  The 5Th Settlement  
4  September        Granville          New Capital City               Cairo

In [32]:
df.info()
display(df.describe(include='all').T)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19924 entries, 0 to 19923
Data columns (total 13 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   price               19924 non-null  float64
 1   type                19924 non-null  object 
 2   bedrooms            19924 non-null  float64
 3   bathrooms           19924 non-null  float64
 4   payment_method      19924 non-null  object 
 5   down_payment        19924 non-null  float64
 6   size_sqm            19924 non-null  float64
 7   down_payment_ratio  19924 non-null  float64
 8   year                19924 non-null  Int64  
 9   month               19924 non-null  object 
 10  area                19924 non-null  object 
 11  city                19924 non-null  object 
 12  governorate         19924 non-null  object 
dtypes: Int64(1), float64(6), object(6)
memory usage: 2.0+ MB


count unique                       top   freq             mean              std        min  \
price               19924.0    NaN                       NaN    NaN  14479857.393295  13298974.193465  1450000.0   
type                  19924      5                 apartment   9814              NaN              NaN        NaN   
bedrooms            19924.0    NaN                       NaN    NaN         2.891387         0.687216        1.0   
bathrooms           19924.0    NaN                       NaN    NaN         2.921351          1.23355        1.0   
payment_method        19924      2                      cash  16062              NaN              NaN        NaN   
down_payment        19924.0    NaN                       NaN    NaN   1514456.596592   1617172.570581        0.0   
size_sqm            19924.0    NaN                       NaN    NaN       201.484263       120.904962       45.0   
down_payment_ratio  19924.0    NaN                       NaN    NaN         0.111483          0.07429        0.0   
year                19924.0   <NA>                      <NA>   <NA>      2025.004316         0.123451     2023.0   
month                 19924     12                    August  11204              NaN              NaN        NaN   
area                  19924   1469                   Marassi    433              NaN              NaN        NaN   
city                  19924    296  5Th Settlement Compounds   3670              NaN              NaN        NaN   
governorate           19924     81               North Coast   4721              NaN              NaN        NaN   

                          25%         50%         75%         max  
price               6000000.0  10200000.0  17500000.0  74240625.0  
type                      NaN         NaN         NaN         NaN  
bedrooms                  3.0         3.0         3.0         7.0  
bathrooms                 2.0         3.0         4.0         7.0  
payment_method            NaN         NaN         NaN         NaN  
down_payment         564000.0   1000000.0   1795000.0   9000000.0  
size_sqm                125.0       170.0       238.0      723.54  
down_payment_ratio        0.1         0.1         0.1         0.5  
year                   2025.0      2025.0      2025.0      2027.0  
month                     NaN         NaN         NaN         NaN  
area                      NaN         NaN         NaN         NaN  
city                      NaN         NaN         NaN         NaN  
governorate               NaN         NaN         NaN         NaN